In [1]:
#Variables
p = 3 # Ha de ser un nombre primer
m = 2 # Un natural qualsevol
q = p^m
F = GF(q) # Cos finit de q elements
n = 5 # n és la longitud del codi, pot ser qualsevol natural menor o igual que q
k = 3 # k és la dimensió i ha de ser més petita que n
r = n - k # r és la redundància del codi
t = RR(r/2).floor() # capacitat correctora

In [2]:
#Definim un llistat de n alphas diferents del cos F
alphas = []
while len(alphas) < n:
    alpha = F.random_element()
    if not (alpha in alphas):
        alphas.append(alpha)
print alphas

[2*z2 + 1, z2 + 1, 1, 2*z2, z2]


In [3]:
#Definim un llistat de n h's diferents de 0 del cos F
h = []
while len(h) < n:
    hi = F.random_element()
    if not (hi == 0):
        h.append(hi)
print h

[2*z2 + 1, 2, 2, 2*z2, z2]


In [4]:
#Definim la matriu de control H dels codis Alternants
H = Matrix(F,r,n,0)
for i in range(r):
    for j in range(n):
        H[i,j] = h[j]*alphas[j]^i
print H

[2*z2 + 1        2        2     2*z2       z2]
[2*z2 + 2 2*z2 + 2        2   z2 + 1   z2 + 1]


In [5]:
# Trobem la matriu generadora G sabent que GH^T=0
G = H.transpose().left_kernel().matrix()

In [6]:
 #Ara, podem codificar qualsevol paraula de F^k
u = [F.random_element() for i in range(k)] # Missatge
m_matrix = Matrix(F,1,k,u) # Missatge vist com a matriu d'una fila
print 'Vull enviar el missatge', u

Vull enviar el missatge [z2 + 2, 0, 0]


In [7]:
#Codifiquem el missatge fent uG
x = m_matrix*G #codifiquem el missatge
print 'El missatge codificat és', x

El missatge codificat és [z2 + 2      0      0 z2 + 1      1]


In [8]:
#Creem errors aleatoris per introduir al missatge
posicions_error = [] # Ens determina en quines coordenades hi haurà error
errors = []
while len(posicions_error) < t: #El codi pot corregir com a molt t errors, aleshores haurem de canviar t coordenades
    index = ZZ.random_element(0,n)
    if not index in posicions_error:
        posicions_error.append(index)
    while len(errors) < t:
        a = F.random_element()
        if not (a == x[0,index]):
            errors.append(a)
print 'posicions error = ', posicions_error
print 'errors = ', errors

posicions error =  [3]
errors =  [z2]


In [9]:
# Introduim els errors al missatge rebut x. El missatge amb errors serà y
y = vector(F,n)
for i in range(n):
    y[i] = x[0,i] #Primer definim y igual a x i li apliquem els errors
for i in range(t):
    y[posicions_error[i]] = errors[i]
print 'El missatge amb errors és:', y

El missatge amb errors és: (z2 + 2, 0, 0, z2, 1)


In [10]:
# Suposem que rebem el missatge anterior, calculem el seu síndrome
sy = y*H.transpose()
print 'El síndrome de y és:', sy

El síndrome de y és: (z2, 2*z2 + 2)


In [11]:
def pes(v):
    t = 0
    for i in range(len(v)):
        if v[i]!=F(0):
            t = t+1
    return t

In [12]:
from itertools import*
# Hem de buscar els líders de les coclasses: són paraules que no pertanyen al codi amb pes mínim
d = dict() # Paraules del cos amb el seu síndrome
for i in product(F, repeat=n):
    v = vector(F,n)
    for j in range(n):
        v[j] = i[j]
    s = tuple((v*H.transpose()).list())
    if not s in d.keys():
        d[s] = v
    else:
        if pes(v)<pes(d[s]): #Agafem les de pes mínim
            d[s] = v

In [13]:
# Hem de trobar el líder de la coclasse que tingui el mateix síndrome que la paraula rebuda
a = d[tuple(sy.list())]

In [14]:
# Finalment, descodifiquem y com c = y - a
c = y - a
print c

(z2 + 2, 0, 0, z2 + 1, 1)
